In [2]:
import pandas as pd
import numpy as np
from openai import OpenAI
import json
import ast

In [87]:
resume_df = pd.read_csv("resume_data.csv")
resume_df = resume_df[['order_id','resume_content']]
resume_df

order_id  \
0     5ffc785db364050012c3e4fa   
1     5ff8945fdd2f9600139ab16a   
2     5ff7cd94dd2f9600139ab137   
3     5ff893a5dd2f9600139ab166   
4     5ff7d77cdd2f9600139ab149   
...                        ...   
1032  63fa56402550d3001349aaa6   
1033  643c7cf9205ec7001b503d22   
1034  650d9be33dc7b3001a2eac1f   
1035  650df55a26f684001a278291   
1036  6532e67b1fdcfd0013a23160   

                                         resume_content  
0     JAMIE MONOZON \n 3150 Crestmoor Drive, San Bru...  
1     LIZANN Thompson\t \n 22941 Spicebush Drive, Cl...  
2     414-429-4468 | umasenthil2000@gmail.com |http:...  
3     KANESHA JON ES  \n 17 Summerfield Place • Nept...  
4     Vivian  N. Ogbolu  (Kristine )  \n 2315 Sandi ...  
...                                                 ...  
1032  Professional Profile \n Finance Professional \...  
1033  Desiree  Matlock  \n Orlando, FL  | (757)  319...  
1034  Amit Nath, MA \n City, ST | (111) 111-1111 | n...  
1035  Hi Brad, \n  \n Thanks for your email and your...  
1036  Amit Nath, MA \n City, ST | (111) 111-1111 | n...  

[1037 rows x 2 columns]

#### extraction prompts

In [147]:
extract_personalInfo = """
Extract the following personal information from the resume given below. Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. Only return final JSON output.
{
  "personalInformation": {
    "firstName": "string",
    "lastName": "string",
    "phoneNumber": "string",
    "email": "email",
    "location": {
      "state": "string",
      "country": "string"
    },
    "linkedinURL": "url",
    "professionalWebsites": ["url"]
  }
}

"""


extract_workExp = """
Extract the following information from the resume given below. Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. You will be rewarded for accurately extracting each and every work experience listed in the resume. Only return final JSON output.
{
  "workExperience": [
    {
      "companyName": "string",
      "startAndEndDates": "date",
      "companyLocation": {
        "state": "string",
        "country": "string"
       },
      "jobTitle": "string",
      "responsibilitiesAndAccomplishments": ["string"]
    }
  ]
}

"""

extract_education = """
Extract the following information from the resume given below. Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. You will be rewarded for accurately extracting each and every education listed in the resume. Only return final JSON output.

{
  "education": [
    {
      "univerityName": "string",
      "graduationDate": "date",
      "degreeTitle": "string"
    }
  ]
}

"""

extract_certifications = """
Extract the following information from the resume given below (if present). Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. "Certifications" are formal credentials granted after completing specific training or passing exams to validate professional skills and knowledge. Do not confuse them for "awards and honors" which recognize exceptional achievements or contributions, often without a formal process or examination.
{
  "certifications": [
    {
      "name": "string",
      "expectedCertificationDate": "date",
      "certificationNumber": "string",
      "issuingAuthority": "string"  
    }
  ]
}
You will be rewarded for accurately extracting the certifications listed in the resume. Only return final JSON output. 

"""

extract_skills = """
Extract the following information from the resume given below (if present) to the best of your abilities. Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. Only return final JSON output.
{
  "skills": ["string"],
  "technical proficiencies": {}
}

Here is an example: 
Input: 
Skills:
Software Development, Project Management,...
Technical Proficiencies:
Programming languages: Java, Python
Development frameworks: Spring, Django, React
Databases: MySQL, PostgreSQL, MongoDB

Output:
{
  "skills": ["Software Development", "Project Management",...],
  "technical proficiencies": {
    "Programming languages": ["Java", "Python"],
    "Development frameworks": ["Spring", "Django", "React"],
    "Databases": ["MySQL", "PostgreSQL", "MongoDB"]
  }
}

"""


extract_affiliations = """
Extract the following information from the resume given below (if present). Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. "Professional Affiliations" refer to memberships or active participation in professional organizations, associations, or societies relevant to one's career or industry. This does not include experiences that are part of professional work experience. It also does not include work that would otherwise count as "volunteer experience" i.e. unpaid work done for community service, charitable organizations, or non-profits. Awards and certifications also strictly do not come under this category.
{
  "professionalAffiliations": [ 
    {
      "organizationName": "string",
      "role": "string",
      "date": "date"
    }
  ]
}
You will be rewarded for accurately extracting the professional affiliations listed in the resume. Only return final JSON output. 

"""


extract_volunteer = """
Extract the following information from the resume given below (if present). Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. "Volunteering Experiences" involve unpaid work done for community service, charitable organizations, or non-profits. This does not include experiences that are part of professional work experience or memberships to professional organizations like IEEE, Society for Human Resource Management, and the like. These also don't include awards or certifications obtained at different organizations. 
{
  "volunteerExperiences": [ 
    {
      "organizationName": "string",
      "role": "string",
      "date": "date"
    }
  ]
}
You will be rewarded for accurately extracting the volunteering experiences listed in the resume. Only return final JSON output. 

"""


extract_awards = """
Extract the following information from the resume given below (if present). Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. "Awards and Honors" refer to recognitions and accolades received for exceptional achievements, performance, or contributions in academic, professional, or extracurricular activities. "Awards and Honors" differ from "certifications" in that they recognize exceptional achievements or contributions, without a formal process or examination, while "certifications" are formal credentials granted after completing specific training or passing exams to validate professional skills and knowledge. 
{
  "awardsAndHonors": [
    {
      "awardName": "string",
      "organization": "string",
      "date": "date"    
  ]
}
You will be rewarded for accurately extracting the awards and honors listed in the resume. Only return final JSON output. 

"""

extract_professionalSummary = """
Extract the following information from the resume given below (only if directly present under a similar heading in the resume). Present the final extracted data in the following JSON format. Ensure no details from the resume are missed during extraction. Only return final JSON output.
{
  "professionalSummary": ["string"]
}
"""

#### resume conversion

In [145]:
def _get_model_output(resume_prompt):
    client =  OpenAI(
    api_key="",
)
    response = client.chat.completions.create(
            model="gpt-3.5-turbo",
            messages = [
        {"role": "system", "content": "You are a resume converter. Given a text resume, your job is to convert it into JSON by extracting relevant fields. Respond only with the JSON output. Do not provide any explanations, comments, or additional text outside the JSON output."},
        {"role": "user", "content": resume_prompt}
    ], 
    response_format={"type": "json_object"}
            )
    result = response.choices[0].message.content
    return result

In [146]:
resume_conversion_prompts = {
    "extract_personalInfo": extract_personalInfo,
    "extract_workExp": extract_workExp,
    "extract_education": extract_education,
    "extract_certifications": extract_certifications,
    "extract_skills": extract_skills,
    "extract_affiliations": extract_affiliations,
    "extract_volunteer": extract_volunteer, 
    "extract_awards": extract_awards,
    "extract_professionalSummary": extract_professionalSummary
}

In [91]:
import time 

json_personalInfo = []
json_workExp = []
json_education = []
json_certifications = []
json_skills = []
json_affiliations = []
json_volunteer = []
json_awards = []
json_professionalSummary = []
for id, row  in resume_df.iterrows():
    start = time.time()
    text_resume = row['resume_content']
    # begin converting to json section-wise
    for conversion_prompt in resume_conversion_prompts.keys():
        converted_sec_json = _get_model_output(
            resume_conversion_prompts[conversion_prompt] + f"Here is the resume:\n{text_resume}"
        )  # get formatted output from chat model
        print (converted_sec_json)
        if conversion_prompt=="extract_personalInfo":
            json_personalInfo.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_workExp":
            json_workExp.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_education":
            json_education.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_certifications":
            json_certifications.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_skills":
            json_skills.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_affiliations":
            json_affiliations.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_volunteer":
            json_volunteer.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_awards":
            json_awards.append(json.loads(json.dumps(converted_sec_json)))
        elif conversion_prompt=="extract_professionalSummary":
            json_professionalSummary.append(json.loads(json.dumps(converted_sec_json)))
    end = time.time()
    print (f"--------------------------------PROCESSED ID {id} IN {end-start} SECONDS--------------------------------")


resume_df["personalInfo"] = json_personalInfo
resume_df["workExp"] = json_workExp
resume_df["education"] = json_education
resume_df["certifications"] = json_certifications
resume_df["skills"] = json_skills
resume_df["professionalAffiliations"] = json_affiliations
resume_df["volunteerExp"] = json_volunteer
resume_df["awardsAndHonors"] = json_awards
resume_df["professionalSummary"] = json_professionalSummary

{
  "personalInformation": {
    "firstName": "Jamie",
    "lastName": "Monozon",
    "phoneNumber": "650.743.9600",
    "email": "jamiemonozon@gmail.com",
    "location": {
      "state": "CA",
      "country": "USA"
    },
    "linkedinURL": "",
    "professionalWebsites": []
  }
}
{
  "workExperience": [
    {
      "companyName": "San Bruno Chamber of Commerce",
      "startAndEndDates": "07/2012 to Current",
      "companyLocation": {
        "state": "CA",
        "country": "USA"
      },
      "jobTitle": "CEO",
      "responsibilitiesAndAccomplishments": [
          "Continue to build a mutually beneficial relationship with the City, YouTube, Walmart.com, Skyline College and other major players in the area to best serve our membership by providing education, marketing and revenue generating opportunities.",
          "Created and instituted the Multi-Chamber Business Expo, Excellence in Business and Community Awards, Dogtoberfest, Community Day in the Park and others.",
      

In [98]:
resume_df.to_csv('resume_extracted.csv')

In [99]:
resume_df

order_id  \
0     5ffc785db364050012c3e4fa   
1     5ff8945fdd2f9600139ab16a   
2     5ff7cd94dd2f9600139ab137   
3     5ff893a5dd2f9600139ab166   
4     5ff7d77cdd2f9600139ab149   
...                        ...   
1032  63fa56402550d3001349aaa6   
1033  643c7cf9205ec7001b503d22   
1034  650d9be33dc7b3001a2eac1f   
1035  650df55a26f684001a278291   
1036  6532e67b1fdcfd0013a23160   

                                         resume_content  \
0     JAMIE MONOZON \n 3150 Crestmoor Drive, San Bru...   
1     LIZANN Thompson\t \n 22941 Spicebush Drive, Cl...   
2     414-429-4468 | umasenthil2000@gmail.com |http:...   
3     KANESHA JON ES  \n 17 Summerfield Place • Nept...   
4     Vivian  N. Ogbolu  (Kristine )  \n 2315 Sandi ...   
...                                                 ...   
1032  Professional Profile \n Finance Professional \...   
1033  Desiree  Matlock  \n Orlando, FL  | (757)  319...   
1034  Amit Nath, MA \n City, ST | (111) 111-1111 | n...   
1035  Hi Brad, \n  \n Thanks for your email and your...   
1036  Amit Nath, MA \n City, ST | (111) 111-1111 | n...   

                                           personalInfo  \
0     {\n  "personalInformation": {\n    "firstName"...   
1     {\n  "personalInformation": {\n    "firstName"...   
2     {\n  "personalInformation": {\n    "firstName"...   
3     {\n  "personalInformation": {\n    "firstName"...   
4     {\n  "personalInformation": {\n    "firstName"...   
...                                                 ...   
1032  {\n  "personalInformation": {\n    "firstName"...   
1033  {\n  "personalInformation": {\n    "firstName"...   
1034  {\n  "personalInformation": {\n    "firstName"...   
1035  {\n  "personalInformation": {\n    "firstName"...   
1036  {\n  "personalInformation": {\n    "firstName"...   

                                                workExp  \
0     {\n  "workExperience": [\n    {\n      "compan...   
1     {\n  "workExperience": [\n    {\n      "compan...   
2     {\n  "workExperience": [\n    {\n      "compan...   
3     {\n  "workExperience": [\n    {\n      "compan...   
4     {\n  "workExperience": [\n    {\n      "compan...   
...                                                 ...   
1032  {\n    "workExperience": [\n        {\n       ...   
1033  {\n  "workExperience": [\n    {\n      "compan...   
1034  {\n  "workExperience": [\n    {\n      "compan...   
1035  {\n  "workExperience": [\n    {\n      "compan...   
1036  {\n  "workExperience": [\n    {\n      "compan...   

                                              education  \
0     {\n  "education": [\n    {\n      "univerityNa...   
1     {\n  "education": [\n    {\n      "univerityNa...   
2     {\n  "education": [\n    {\n      "univerityNa...   
3     {\n  "education": [\n    {\n      "univerityNa...   
4     {\n  "education": [\n    {\n      "univerityNa...   
...                                                 ...   
1032  {\n  "education": [\n    {\n      "univerityNa...   
1033  {\n  "education": [\n    {\n      "univerityNa...   
1034  {\n  "education": [\n    {\n      "universityN...   
1035                            {\n  "education": []\n}   
1036  {\n  "education": [\n    {\n      "universityN...   

                                         certifications  \
0                        {\n    "certifications": []\n}   
1     {\n  "certifications": [\n    {\n      "name":...   
2     {\n\t"certifications": [{\n\t\t"name": "Certif...   
3                          {\n  "certifications": []\n}   
4     {\n  "certifications": [\n    {\n      "name":...   
...                                                 ...   
1032  {\n  "certifications": [\n    {\n      "name":...   
1033  {\n  "certifications": [\n    {\n      "name":...   
1034  {\n  "certifications": [\n    {\n      "name":...   
1035                       {\n  "certifications": []\n}   
1036  {\n  "certifications": [\n    {\n      "name":...   

                                                 skills  \
0     {\n